In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import sys

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


#Select Dataset

In [ ]:
#dataset_name = "Multi"
dataset_name = "ARAS"

# Reading in the Data and processing

In [ ]:
if dataset_name == "ARAS":
  df_clean = pd.read_csv("/content/gdrive/MyDrive/Colab Notebooks/processed_data/Aras_HouseA.csv")
elif dataset_name == "Multi":
  df_clean = pd.read_csv("/content/gdrive/MyDrive/Colab Notebooks/processed_data/3_months_data.csv")

In [ ]:
df_clean

Unnamed: 0  sensor_id  value   time  old_sen
0               0       5889      1     49        3
1               1       5889      0    252        3
2               2       5889      1    301        3
3               3       5889      0    504        3
4               4       5889      1    505        3
...           ...        ...    ...    ...      ...
53873       53873       7125      0  85987       17
53874       53874       5888      0  85992       11
53875       53875       5893      1  86001       15
53876       53876       5893      0  86004       15
53877       53877       5889      1  86015        4

[53878 rows x 5 columns]

# Convertion to format for the SPEED algorithm

In [ ]:
def create_on_off_Multi_char():
    dic_on_off = {}
    dic_on_off[5895] = ["a","A"]
    dic_on_off[7125] = ["b", "B"]
    dic_on_off[5896] = ["c", "C"]
    dic_on_off[6253] = ["d", "D"]
    dic_on_off[6632] = ["e", "E"]
    dic_on_off[6633] = ["f", "F"]
    dic_on_off[6635] = ["g", "G"]
    dic_on_off[6896] = ["h", "H"]
    dic_on_off[5887] = ["i", "I"]
    dic_on_off[5888] = ["j", "J"]
    dic_on_off[5889] = ["k", "K"]
    dic_on_off[5893] = ["l", "L"]
    return dic_on_off

In [ ]:
def create_on_off_Multi_int():
    dic_on_off = {}
    dic_on_off[5895] = [0,1]
    dic_on_off[7125] = [2, 3]
    dic_on_off[5896] = [4,5]
    dic_on_off[6253] = [6, 7]
    dic_on_off[6632] = [8, 9]
    dic_on_off[6633] = [10, 11]
    dic_on_off[6635] = [12, 13]
    dic_on_off[6896] = [14, 15]
    dic_on_off[5887] = [16, 17]
    dic_on_off[5888] = [18, 19]
    dic_on_off[5889] = [20, 21]
    dic_on_off[5893] = [22, 23]
    return dic_on_off

In [ ]:
dic_on_off = create_on_off_Multi_char()
dic_on_off

{5887: ['i', 'I'],
 5888: ['j', 'J'],
 5889: ['k', 'K'],
 5893: ['l', 'L'],
 5895: ['a', 'A'],
 5896: ['c', 'C'],
 6253: ['d', 'D'],
 6632: ['e', 'E'],
 6633: ['f', 'F'],
 6635: ['g', 'G'],
 6896: ['h', 'H'],
 7125: ['b', 'B']}

In [ ]:
dic_on_off_int = create_on_off_Multi_int()
dic_on_off_int

{5887: [16, 17],
 5888: [18, 19],
 5889: [20, 21],
 5893: [22, 23],
 5895: [0, 1],
 5896: [4, 5],
 6253: [6, 7],
 6632: [8, 9],
 6633: [10, 11],
 6635: [12, 13],
 6896: [14, 15],
 7125: [2, 3]}

In [ ]:
def add_event_col(df, dic):

    add = []

    for index, row in df.iterrows():

        sensor = row["sensor_id"]
        value = int(row["value"])

        add.append(dic[sensor][value])

    df["event"] = np.array(add)
    return df

In [ ]:
df = add_event_col(df_clean, dic_on_off)
if dataset_name == "ARAS":
  df = df[["time", "event"]]
elif dataset_name == "Multi":
  df = df[["time_scal", "event"]]

In [ ]:
df["event"].value_counts()

k    6639
K    6638
a    3815
A    3814
i    3576
I    3575
l    3058
L    3057
c    1752
C    1751
e    1344
E    1343
d    1055
D    1054
b     374
B     374
j     344
J     343
f     111
F     110
h      38
H      37
g      11
G      10
Name: event, dtype: int64

#The SPEED Algorithm

# df and sequence list

In [ ]:
df

time_scal event
0       0.070203     a
1       0.070204     k
2       0.070204     c
3       0.070204     d
4       0.070204     i
...          ...   ...
44218   0.037144     e
44219   0.037148     E
44220   0.037150     e
44221   0.037156     E
44222   0.037161     e

[44223 rows x 2 columns]

In [ ]:
sequence_list = df.values.tolist()    # [timestamp, single event]
print("length of total sequence:", len(sequence_list))
print("length of training sequence:", int(len(sequence_list)*0.8))
print("length of testing sequence:", int(len(sequence_list)*0.2))

sequence_list.head()

NameError: ignored

In [ ]:
training_data = sequence_list[:int(len(sequence_list)*0.8)]
testing_data = sequence_list[int(len(sequence_list)*0.8):]
print("training:", len(training_data))
print("testing:", len(testing_data))

training: 35378
testing: 8845


#Create Episodes

In [ ]:
caps = ["A", "B", "C", "D", "E", "F", "G", "H", "I", "J", "K", "L"]   # turning on
lows = ["a", "b", "c", "d", "e", "f", "g", "h", "i", "j", "k", "l"]   # turning off
all_actions = caps + lows

In [ ]:
def create_episodes(episode_seq, episode_list, sequence_list):
  for item_id, item in enumerate(sequence_list):
    item_time = item[0]
    item_event = item[1]
    episode_seq += item_event
    if item_event in caps:      # start of episode
      episode = item_event
      #print("start of episode: ", item_event)
      opp_event = False
      plus_id = 1
      while opp_event == False and item_id+plus_id < len(sequence_list)-1:
        next_item = sequence_list[item_id + plus_id]
        if next_item[1] == item_event.lower():        # end of episode
          episode += next_item[1]
          episode_list.append(episode)
          opp_event = True
        else:
          episode += next_item[1]
          plus_id += 1
    if item_event in lows:      # start of episode
      episode = item_event
      #print("start of episode: ", item_event)
      opp_event = False
      plus_id = 1
      while opp_event == False and item_id+plus_id < len(sequence_list)-1:
        next_item = sequence_list[item_id + plus_id]
        if next_item[1] == item_event.upper():        # end of episode
          episode += next_item[1]
          episode_list.append(episode)
          opp_event = True
        else:
          episode += next_item[1]
          plus_id += 1
      #print("end of episode, episode: ", episode)

  return episode_list, episode_seq

In [ ]:
# tree[key] = [occurence of key, {"seq1 following key":occur of seq1, "seq2 following key":occur of seq2}]
# episode_seq = sub_episode_seq   # to be deleted later after testing

def create_dict_for_tree(episode_list):
  for ep_id, ep in enumerate(episode_list):
    #print("ep[0]: ", ep[0])
    if ep[0] not in dict_tree.keys():
      dict_tree[ep[0]] = [1, {}]
    else:
      dict_tree[ep[0]][0] += 1
      cumu_seq = ""
      for next_item in ep[1:]:
        cumu_seq += next_item
        if cumu_seq in dict_tree[ep[0]][1].keys():
          dict_tree[ep[0]][1][cumu_seq] += 1
        else:
          dict_tree[ep[0]][1][cumu_seq] = 1

  return dict_tree


In [ ]:
episode_seq = ""
episode_list = list()
dict_tree = dict()     # [occurences of the alphabet, [[list of things that follows, occurences]]]
episode_list, episode_seq = create_episodes(episode_seq, episode_list, training_data)
dict_tree = create_dict_for_tree(episode_list)

In [ ]:
episode_list

['akcdilA',
 'kcdilALlLlLDdDdlLDdlaLlALlaAaAaAaAaAaAaAaAaAaAaAaAaIiIiAaIiIiIiIiIiIiIiIiAaIiIiIiIAaiIiIiIiIAiIiIaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaALiDdlIaAegfaAaAaAaCAcCaAaAacACaAcCcaAaAaACcaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaACcaAaAaAaAaAaAaAaAaAaAaAaAaAaAaALilCcCIaAaAcCLlaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaiIAiaIiIiIiIiAIiIiIiIiIiIiaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAacACaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAaAcaACcCcCcCaAcLlLDdEeEDeEdeEeEeEDedlEeEeEeLlEeEeEeLlLalALalLlEeAEeLlaAaALalALlLlaAaAaAaAaAaAaAaAaAaAaAaALlLDdDdDdaAlLlLlLlLlLlLlLlLlLlLlLlLlaLlALlLlLlLlLalLlALlLlLlLlLlLlLlaLlLAlLlLlLlLlLlLlLlLlLlLlLlaLlLAlLlLlLDdaAaAlLlLlLlLlLlLlaAaAaAaAaAaAaAaAaAaAaAaAaAaALFDdDdaDdfADdFDdDdfDdlLlLlaAaAaAaAaAaAaAaAaAaAaAaALlaAaAaAaAaAaAaAIiIia

In [ ]:
dict_tree.keys()

dict_keys(['a', 'k', 'c', 'd', 'i', 'l', 'A', 'L', 'D', 'I', 'e', 'g', 'f', 'C', 'E', 'F', 'G', 'K', 'j', 'J', 'h', 'H', 'b', 'B'])

In [ ]:
dict_tree

{'A': [3814,
  {'L': 185,
   'Ll': 112,
   'Lla': 17,
   'a': 3205,
   'i': 34,
   'iI': 31,
   'iIi': 29,
   'iIiI': 29,
   'iIiIa': 1,
   'Li': 14,
   'LiD': 4,
   'LiDd': 4,
   'LiDdl': 1,
   'LiDdlI': 1,
   'LiDdlIa': 1,
   'e': 3,
   'eg': 1,
   'egf': 1,
   'egfa': 1,
   'c': 74,
   'cC': 43,
   'cCa': 18,
   'C': 63,
   'Ca': 15,
   'cCc': 21,
   'cCca': 4,
   'Cc': 46,
   'Cca': 9,
   'Lil': 4,
   'LilC': 1,
   'LilCc': 1,
   'LilCcC': 1,
   'LilCcCI': 1,
   'LilCcCIa': 1,
   'cCL': 2,
   'cCLl': 2,
   'cCLla': 1,
   'ia': 1,
   'I': 28,
   'Ii': 24,
   'IiI': 23,
   'IiIi': 23,
   'IiIiI': 20,
   'IiIiIi': 20,
   'IiIiIiI': 19,
   'IiIiIiIi': 19,
   'IiIiIiIiI': 16,
   'IiIiIiIiIi': 15,
   'IiIiIiIiIiI': 15,
   'IiIiIiIiIiIi': 15,
   'IiIiIiIiIiIia': 2,
   'ca': 14,
   'CcC': 26,
   'CcCc': 23,
   'CcCcC': 16,
   'CcCcCc': 15,
   'CcCcCcC': 8,
   'CcCcCcCa': 1,
   'cL': 14,
   'cLl': 6,
   'cLlL': 2,
   'cLlLD': 1,
   'cLlLDd': 1,
   'cLlLDdE': 1,
   'cLlLDdEe': 1,
   'cLlLDdE

#Create nested list as stat tree

In [ ]:
# dictionary created above, used to map to decision tree
for key, item in dict_tree.items():
  print("root: ", key, "\tnumber of times as a root: ", item[0], "\tnumber of children: ", len(item[1]))

root:  a 	number of times as a root:  3814 	number of children:  2036
root:  k 	number of times as a root:  4610 	number of children:  13115
root:  c 	number of times as a root:  1339 	number of children:  17352
root:  d 	number of times as a root:  951 	number of children:  30505
root:  i 	number of times as a root:  2552 	number of children:  20188
root:  l 	number of times as a root:  2712 	number of children:  21377
root:  A 	number of times as a root:  3814 	number of children:  9272
root:  L 	number of times as a root:  2712 	number of children:  2476
root:  D 	number of times as a root:  951 	number of children:  59
root:  I 	number of times as a root:  2551 	number of children:  7272
root:  e 	number of times as a root:  1094 	number of children:  29572
root:  g 	number of times as a root:  9 	number of children:  24455
root:  f 	number of times as a root:  92 	number of children:  33728
root:  C 	number of times as a root:  1339 	number of children:  5127
root:  E 	number of t

In [ ]:
dict_tree['A']

[3814,
 {'L': 185,
  'Ll': 112,
  'Lla': 17,
  'a': 3205,
  'i': 34,
  'iI': 31,
  'iIi': 29,
  'iIiI': 29,
  'iIiIa': 1,
  'Li': 14,
  'LiD': 4,
  'LiDd': 4,
  'LiDdl': 1,
  'LiDdlI': 1,
  'LiDdlIa': 1,
  'e': 3,
  'eg': 1,
  'egf': 1,
  'egfa': 1,
  'c': 74,
  'cC': 43,
  'cCa': 18,
  'C': 63,
  'Ca': 15,
  'cCc': 21,
  'cCca': 4,
  'Cc': 46,
  'Cca': 9,
  'Lil': 4,
  'LilC': 1,
  'LilCc': 1,
  'LilCcC': 1,
  'LilCcCI': 1,
  'LilCcCIa': 1,
  'cCL': 2,
  'cCLl': 2,
  'cCLla': 1,
  'ia': 1,
  'I': 28,
  'Ii': 24,
  'IiI': 23,
  'IiIi': 23,
  'IiIiI': 20,
  'IiIiIi': 20,
  'IiIiIiI': 19,
  'IiIiIiIi': 19,
  'IiIiIiIiI': 16,
  'IiIiIiIiIi': 15,
  'IiIiIiIiIiI': 15,
  'IiIiIiIiIiIi': 15,
  'IiIiIiIiIiIia': 2,
  'ca': 14,
  'CcC': 26,
  'CcCc': 23,
  'CcCcC': 16,
  'CcCcCc': 15,
  'CcCcCcC': 8,
  'CcCcCcCa': 1,
  'cL': 14,
  'cLl': 6,
  'cLlL': 2,
  'cLlLD': 1,
  'cLlLDd': 1,
  'cLlLDdE': 1,
  'cLlLDdEe': 1,
  'cLlLDdEeE': 1,
  'cLlLDdEeED': 1,
  'cLlLDdEeEDe': 1,
  'cLlLDdEeEDeE': 1,
  'c

In [ ]:
def tree_search(tree, parent_seq, node_char, node_count):
  # tree =   [str, int, list] or [str, int]
  check_layer = tree
  for char in parent_seq:
    for item in check_layer:
      #print("now layer: ", check_layer, "item: ", item, "matching char: ", char, "parent seq: ", parent_seq)
      if type(item) == list and item[0] == char:
        if type(item[-1]) == list:
          #print("append to: ", item, "check layer: ", check_layer, "TRIGGERED HERE**")   # next layer would be deeper in the tree
          check_layer = check_layer[-1]
        else:
          #print("append to: ", item, "check layer: ", check_layer, "TRIGGERED HERE")     # next layer would be the most shallow subtree layer
          item.append([node_char, node_count])
  return tree

In [ ]:
def count_nodes(node_dict, node):
  if node in caps or node in lows:
    if node in node_dict:
      node_dict[node] += 1
    else:
      node_dict[node] = 1
  return node_dict

#The Tree

In [ ]:
sys.setrecursionlimit(100000)

In [ ]:
the_tree = list()
count_of_all_nodes = dict()
#root_dict = dict()

print("root nodes", "\t[subtrees]")

for key, item in dict_tree.items(): # key: root node (always caps eg. ABC, one of the 12)
  key_list = item[1].keys()
  sub_tree = list()
  checking = []
  check_now = ""
  count_nodes(count_of_all_nodes, key)
  for sub_key in key_list:  # sub_key: the first alphabet following the root (could be upper/lower case)
    if len(checking) == 0 or len(sub_key) == 1:   # adding the first node after the root
        checking.append(sub_key)    # add into the list of existing nodes (for later checking)
        check_now = sub_key
        sub_tree.append([check_now, item[1][sub_key]])    # adds to subtree
        count_nodes(count_of_all_nodes, item[1][sub_key])
    elif sub_key.startswith(checking[-1]):        # match to the last node, if True the next node should be a child of the last one
      append_node_char = sub_key[len(checking[-1]):]
      if len(append_node_char) == 1:
        #print("sub_key: ", sub_key, "checking: ", check_now, "append: ", append_node_char, "occur: ", item[1][sub_key])
        sub_tree = tree_search(sub_tree, check_now, append_node_char, item[1][sub_key])
        count_nodes(count_of_all_nodes, append_node_char)
      check_now = sub_key
      checking.append(check_now)
    elif sub_key.startswith(checking[-1]) == False:
      re_check_id = -2  #check one more index back
      check_now = checking[re_check_id]
      while check_now != checking[0]:
        if sub_key.startswith(checking[re_check_id]):
          append_node_char = sub_key[len(checking[re_check_id]):]
          sub_tree = tree_search(sub_tree, check_now, append_node_char, item[1][sub_key])
          count_nodes(count_of_all_nodes, append_node_char)
          check_now = sub_key
          checking.append(check_now)
          break
        else:
          #print("*RECHECK*", "sub_key: ", sub_key, "checking: ", check_now, "append: ", "nothing")
          re_check_id -= 1
          check_now = checking[re_check_id]
  the_tree.append([key, count_of_all_nodes[key], sub_tree])
  #root_dict[key] = sub_tree

  print(key, "\t", sub_tree)

print("count of all nodes")
count_of_all_nodes

root nodes 	[subtrees]
a 	 [['L', 74, ['l', 35, ['A', 29]]], ['A', 3551], ['I', 21, ['i', 18, ['I', 12, ['i', 12, ['A', 3]]]]], ['i', 19, ['I', 14, ['i', 10, ['I', 9, ['i', 9, ['I', 9, ['i', 8, ['I', 6, ['A', 2]]]]]]]]], ['C', 29, ['A', 11]], ['c', 19, ['A', 8]], ['l', 46, ['A', 26]], ['D', 9, ['d', 5, ['f', 1, ['A', 1]]]], ['F', 1, ['A', 1]], ['f', 2, ['A', 2]], ['d', 4, ['A', 2]], ['k', 20, ['K', 15, ['A', 7]]], ['K', 8, ['A', 2]], ['E', 5, ['e', 5, ['E', 4, ['e', 3, ['E', 1, ['e', 1, ['A', 1]]]]]]], ['J', 3, ['j', 3, ['A', 3]]], ['j', 1, ['A', 1]], ['b', 1, ['B', 1, ['b', 1, ['B', 1, ['b', 1, ['B', 1, ['b', 1, ['B', 1, ['b', 1, ['B', 1, ['b', 1, ['B', 1, ['L', 1, ['l', 1, ['L', 1, ['l', 1, ['L', 1, ['l', 1, ['L', 1, ['l', 1, ['L', 1, ['l', 1, ['L', 1, ['b', 1, ['l', 1, ['L', 1, ['l', 1, ['L', 1, ['l', 1, ['L', 1, ['l', 1, ['B', 1, ['L', 1, ['E', 1, ['l', 1, ['e', 1, ['L', 1, ['E', 1, ['e', 1, ['E', 1, ['e', 1, ['E', 1, ['e', 1, ['E', 1, ['e', 1, ['D', 1, ['E', 1, ['d', 1, ['e', 1, [

{'A': 29891,
 'B': 1788,
 'C': 11579,
 'D': 7566,
 'E': 8967,
 'F': 712,
 'G': 90,
 'H': 277,
 'I': 20948,
 'J': 2395,
 'K': 36575,
 'L': 21912,
 'a': 30124,
 'b': 1859,
 'c': 11472,
 'd': 7219,
 'e': 8879,
 'f': 693,
 'g': 92,
 'h': 283,
 'i': 20939,
 'j': 2242,
 'k': 36612,
 'l': 21677}

In [ ]:
total_count_of_nodes = 0
for key, item in count_of_all_nodes.items():
  total_count_of_nodes += item

print(total_count_of_nodes)
print(len(count_of_all_nodes))

284791
24


In [ ]:
the_tree[1]

['k',
 30,
 [['L',
   113,
   ['a',
    1,
    ['A',
     1,
     ['D',
      1,
      ['d',
       1,
       ['D',
        1,
        ['d',
         1,
         ['l',
          1,
          ['L',
           1,
           ['l',
            1,
            ['L',
             1,
             ['a',
              1,
              ['l',
               1,
               ['A',
                1,
                ['a',
                 1,
                 ['A',
                  1,
                  ['a',
                   1,
                   ['C',
                    1,
                    ['c',
                     1,
                     ['A',
                      1,
                      ['a',
                       1,
                       ['A',
                        1,
                        ['a',
                         1,
                         ['A',
                          1,
                          ['L',
                           1,
                           ['D',
    

In [ ]:
len(the_tree)

24

#Prediction with reference to tree

modify below

In [ ]:
def get_store_list(target_count_in_term_node, check_seq, target, the_tree, check_subseq, check_layer, store_for_prob, counter):
        for id, thing in enumerate(check_layer):
          if counter == 0:
            if thing == target:
              #print("target: ", thing, check_layer[id+1])
              target_count_in_term_node = check_layer[id+1]
              break
          
          if type(thing) == str and len(check_subseq) == 1:
            #print(thing, check_subseq)
            if thing == check_subseq[0]:
              #print("found match: ", thing, "in node", check_layer)
              # store numbers
              store_for_prob.append((thing, check_layer[1]))
              #print("append:", (thing, check_layer[1]))
          elif type(thing) == int:
            continue
          elif type(thing[-1]) == list and len(check_subseq)>0:
            if thing[0] == check_subseq[0]:
              check_layer = thing[2]
              #print("found match: ", thing)
              # store nums
              store_for_prob.append((thing[0],thing[1]))
              #print("append:", (thing[0],thing[1]))
        return store_for_prob, target_count_in_term_node


In [ ]:
# test and modify here
def stored_for_prob(target_count_in_term_node, check_seq, target, the_tree):
  store_for_prob = list()
  for root in the_tree:
    if root[0] == check_seq[0]:
      #print(root[0], root)
      root_subtree = root
      #print("root_subtree:", root)
      #print("branches to", root[0], ":", len(root[2]))

      check_subseq = check_seq[1:]
      counter = len(check_subseq)
      check_layer = root[2]

      while counter > -2:
        for sub_item in check_layer:
          #print("counter: ", counter, "check_subseq: ", check_subseq, "check layer: ", sub_item)
          store_for_prob, target_count_in_term_node = get_store_list(target_count_in_term_node, check_seq, target, the_tree, check_subseq, sub_item, store_for_prob, counter)
          check_subseq = check_subseq[1:]
        counter -= 1
  return(store_for_prob, target_count_in_term_node, root_subtree)

In [ ]:
def prob(root, target, check_seq, store_for_prob, target_count_in_term_node, root_subtree):
  target_in_all_nodes = count_of_all_nodes[target]/total_count_of_nodes
  prob = (target_count_in_term_node/root_subtree[1])*target_in_all_nodes
  prob_output = prob

  for item in store_for_prob:
    new_prob = (target_count_in_term_node/item[1])*prob_output
    #print(item, "update:", target_count_in_term_node, "/", item[1], "*", prob_output)
    prob_output = new_prob
    #print("prob:" , prob_output)

  return prob_output

In [ ]:
def prob_of_target(check_seq, target, the_tree, total_count_of_nodes):
  root = check_seq[0]
  root_subtree = list()
  store_for_prob = list()
  target_count_in_term_node = 0

  store_for_prob, target_count_in_term_node, root_subtree = stored_for_prob(target_count_in_term_node, check_seq, target, the_tree)

  #print("store_for_prob:", store_for_prob)
  #print("target_count_in_term_node", target_count_in_term_node)
  #print("root_subtree", root_subtree)

  target_in_all_nodes = count_of_all_nodes[target]/total_count_of_nodes
  #print(target_in_all_nodes)
  '''
  print("Given sequence:", check_seq)
  print("Predict probability for:", target)
  print("subtree node counts stored for calculation:", store_for_prob)
  print("total number of nodes in the tree:", total_count_of_nodes)
  print("count of target node following the subtree:", target_count_in_term_node)
  print("count of target in the entire tree:", count_of_all_nodes[target])
  print(root_subtree[0], root_subtree[1], len(root_subtree[2]))
  '''

  prob_output = prob(root, target, check_seq, store_for_prob, target_count_in_term_node, root_subtree)

  return prob_output

In [ ]:
# for single instance
check_seq = "Li"
target = "D"
the_prob = prob_of_target(check_seq, target, the_tree, total_count_of_nodes)
print(the_prob)

0.000839345188488137


In [ ]:
# given history, prob of all next actions, and prediction of most likely one
check_seq = "B"
predict_prob = list()

for act in all_actions:
  target = act
  if target in count_of_all_nodes.keys():
    the_prob = prob_of_target(check_seq, target, the_tree, total_count_of_nodes)
    predict_prob.append((act, the_prob))
  else:
    predict_prob.append((act, 0))

#print(predict_prob)

prediction = max(predict_prob, key=lambda x:x[1])
#print(prediction)

print("Given sequence:", check_seq)
print("Predicted next action, probability:", prediction)


Given sequence: B
Predicted next action, probability: ('L', 0.002538868784005716)


In [ ]:
prediction = max(predict_prob, key=lambda x:x[1])
print(prediction)

('L', 0.002538868784005716)


# Looping through the dataset for accuracy scores

In [ ]:
# for reference
'''
training_data = sequence_list[:int(len(sequence_list)*0.8)]
testing_data = sequence_list[int(len(sequence_list)*0.8):]
print("training:", len(training_data))
print("testing:", len(testing_data))
print("number of episodes:", len(episode_list))
'''
testing_sequence = ""

for item in testing_data:
  testing_sequence += item[1]


print(testing_sequence)

kKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKiIiIiIiIiIiIiIiIiIiBCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcLEeEeEeEDdeEDeEdeEelEeEeEeELelLlLlLlLlLlLlLlLlCcLDdDdlLlLlLlLlLlLlLlLlLlLlLDdlbBbBkbBLDdlLlLKkKkKkKkKkKkKkKkKkKkKkKklKkLKkKkKkKkKkKkKkKkKkKkKkKkKkFKkKkKkKkKkKkKkKkKkKkKkKkKkKlfkKLlLFlfLlLDdlLDdlbBLDdlLEDdeDEedEeEeEeEeEeEeEeEeEelLlEeEeEeEeEeEeEeEeEeCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcIiIiIkLlbKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKBCcCcCcCcCcCcCcCkKcCcbBkLiDdlLlLIlKkCcCcbBbBKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKbkKBbBkJjKkKkKLkKkKkKkKkGKkKkKkKkKkKigIkKiIlLlLlLlLlLlLlLlkCcCcCcCcCcCcbKkBCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcbBCcCcCiIiIiIiIiIiIiIiIiIiIiIiIiIicCIiIiIiIiIiIiIiIiIiIiIicCcCcJjbBKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkK

In [ ]:
def get_next_act_prediction(check_seq, the_tree, total_count_of_nodes, all_actions):
  check_seq = check_seq
  predict_prob = list()

  for act in all_actions:
    target = act
    if target in count_of_all_nodes.keys():
      the_prob = prob_of_target(check_seq, target, the_tree, total_count_of_nodes)
      predict_prob.append((act, the_prob))
    else:
      predict_prob.append((act, 0))

  prediction = max(predict_prob, key=lambda x:x[1])

  return predict_prob, prediction

In [ ]:
# testing on testing data episodes
'''
print("training:", len(training_data))
print("testing:", len(testing_data))
print("number of episodes:", len(episode_list))
'''

# testing on sequence
testing_sequence = ""
for item in testing_data:
  testing_sequence += item[1]
print(testing_sequence)

# testing on episodes
test_episode_seq = ""
test_episode_list = list()
test_episode_list, test_episode_seq = create_episodes(episode_seq, episode_list, testing_data)

kKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKiIiIiIiIiIiIiIiIiIiBCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcLEeEeEeEDdeEDeEdeEelEeEeEeELelLlLlLlLlLlLlLlLlCcLDdDdlLlLlLlLlLlLlLlLlLlLlLDdlbBbBkbBLDdlLlLKkKkKkKkKkKkKkKkKkKkKkKklKkLKkKkKkKkKkKkKkKkKkKkKkKkKkFKkKkKkKkKkKkKkKkKkKkKkKkKkKlfkKLlLFlfLlLDdlLDdlbBLDdlLEDdeDEedEeEeEeEeEeEeEeEeEelLlEeEeEeEeEeEeEeEeEeCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcIiIiIkLlbKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKBCcCcCcCcCcCcCcCkKcCcbBkLiDdlLlLIlKkCcCcbBbBKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKbkKBbBkJjKkKkKLkKkKkKkKkGKkKkKkKkKkKigIkKiIlLlLlLlLlLlLlLlkCcCcCcCcCcCcbKkBCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcCcbBCcCcCiIiIiIiIiIiIiIiIiIiIiIiIiIicCIiIiIiIiIiIiIiIiIiIiIicCcCcJjbBKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkKkK

In [ ]:
check_seq = "L"
predict_prob, prediction = get_next_act_prediction(check_seq, the_tree, total_count_of_nodes, all_actions)

print("Given sequence:", check_seq)
print("Probability of next action:\n", predict_prob)
print("Prediction of next action:\n", prediction)

Given sequence: L
Probability of next action:
 [('A', 0.0004753312669767272), ('B', 3.3848869358446334e-06), ('C', 1.753628896203356e-05), ('D', 0.000839345188488137), ('E', 0.0002512381214066212), ('F', 7.548222142393581e-06), ('G', 1.3630417191320672e-07), ('H', 6.292709269993043e-07), ('I', 0.0004203635806711285), ('J', 9.97481502514842e-06), ('K', 9.693687670577431e-05), ('L', 0.0), ('a', 0.0006159040312070158), ('b', 4.927017191962664e-06), ('c', 3.040491728143931e-05), ('d', 2.7332772695595535e-06), ('e', 4.370328236507141e-05), ('f', 2.6238553093292294e-06), ('g', 3.4833288377819494e-08), ('h', 4.2860089612708335e-07), ('i', 0.0005866705725586306), ('j', 3.3954883714378828e-06), ('k', 0.00013862134283573123), ('l', 0.016406601121085003)]
Prediction of next action:
 ('l', 0.016406601121085003)


In [ ]:
# example of moving windows
# *******not actual predictions
window_size = [1,2,3,4,5,6,7,8,9,10]
total_pred = 0
correct_pred = 0

for ws in window_size:
  total_pred = 0
  correct_pred = 0

  print("In window size", ws, "\t For example, given:", testing_sequence[0:0+ws], "... predict", testing_sequence[0+ws+1])


In window size 1 	 For example, given: k ... predict k
In window size 2 	 For example, given: kK ... predict K
In window size 3 	 For example, given: kKk ... predict k
In window size 4 	 For example, given: kKkK ... predict K
In window size 5 	 For example, given: kKkKk ... predict k
In window size 6 	 For example, given: kKkKkK ... predict K
In window size 7 	 For example, given: kKkKkKk ... predict k
In window size 8 	 For example, given: kKkKkKkK ... predict K
In window size 9 	 For example, given: kKkKkKkKk ... predict k
In window size 10 	 For example, given: kKkKkKkKkK ... predict K


In [ ]:
window_size = [1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30]
total_pred = 0
correct_pred = 0
all_pred = 0
all_correct_pred = 0

for ws in window_size:
  total_pred = 0
  correct_pred = 0

  for id, item in enumerate(testing_sequence):
    
    total_pred += 1
    check_seq = testing_sequence[id:id+ws]
    if id < len(testing_sequence)-ws-1:
      true_tag = testing_sequence[id+ws]
    else:
      break
    predict_prob, prediction = get_next_act_prediction(check_seq, the_tree, total_count_of_nodes, all_actions)

    if prediction[0] == true_tag:
      correct_pred += 1

      #print("Given sequence:", check_seq)
      #print("Probability of next action:\n", predict_prob)
      #print("Prediction of next action:", prediction, "\tActual next action:", true_tag)
  
  all_pred += total_pred
  all_correct_pred += correct_pred
  print("Window size", ws, "\tAccuracy:", correct_pred, "/", total_pred, "=", correct_pred/total_pred)

print("Accuracy:", all_correct_pred, "/", all_pred, "=", correct_pred/total_pred)
